# Exporting data from OSM


**OpenStreetMap** is a collaborative, open-source mapping project that provides free, editable geographic data for the entire world. It’s often called the “Wikipedia of maps” because anyone can contribute — and millions of users do.

The data includes a wide range of real-world features such as:

- Roads, buildings, parks, rivers
- Public transport stops, bike lanes, and walking paths
- Points of interest like schools, hospitals, cafes, and more

Thanks to its openness, flexibility, and global coverage, OSM has become one of the **most widely used** spatial data sources — powering applications in urban planning, transportation, humanitarian response, and research. (You can fin more Open Data Sources [here](https://bella-mir.github.io/openSpData/))

And the most of the analsysis in this course will be based on this data

OpenStreetMap data can be exported in many ways — through web interfaces, GIS software, or APIs.
But since we're working in Python, we can fetch OSM data **directly in our Jupyter Notebook**, which makes the workflow faster and fully reproducible.

To do this, we'll use a powerful library called **OSMnx**


### Import libraries


In [1]:
import osmnx as ox

- [**OSMnx**](https://osmnx.readthedocs.io/) (`osmnx`) — a Python library for downloading, analyzing, and visualizing **OpenStreetMap** data.
  It allows you to easily retrieve geospatial features such as **buildings**, **street networks**, and **boundaries** by place name or coordinates. OSMnx integrates smoothly with `GeoPandas` and is ideal for urban analysis, network science, and working with real-world geographic data — all directly within your Python environment.


### Defining the area


First, we need to define the area for which we want to get the data. Let’s choose the Central District of Saint Petersburg.
We’ll use the `geocode_to_gdf` function to retrieve the district boundaries.


In [2]:
admin_district = ox.geocode_to_gdf('Wieden, Vienna')

Let’s see what we’ve got. In the `explore` method, we'll set the `tiles` parameter to change the default OSM basemap to **Positron**.


In [3]:
admin_district.explore(tiles='cartodbpositron')

Incredible! But this is exactly what we need — the boundaries of the Central District of Saint Petersburg.


### Exporting features


Now let's try exporting building data for the Central District.
To do this, we'll create a `tags` variable and specify the key for the objects we need — **buildings**.
We'll then pass the district name and the tags to the `geometries_from_place` function.

You can read more about OSM keys and values [here](https://wiki.openstreetmap.org/wiki/Map_features).


In [4]:
tags = {'building': True}   

buildings = ox.features_from_place('Wieden, Vienna', tags)

buildings.explore(tiles='cartodbpositron',tooltip=None)

We’ve got the buildings!

Now let’s filter the data to include only **Polygon** and **MultiPolygon** geometries.


In [5]:
buildings = buildings.loc[buildings.geom_type.isin(['Polygon', 'MultiPolygon'])]

And now we can safely save the data!

**Spoiler** — an error will occur during saving because some fields contain data in **list** format.
This format isn't supported for saving, so we'll fix it by converting those fields to **strings**.


This loop checks each column in the `buildings` GeoDataFrame to see if it contains **list-type values**.
Some columns in OSM data (especially tags like `amenity`, `building:use`, etc.) can contain lists — for example, when multiple values are assigned to one feature.

However, file formats like **GeoJSON** or **Shapefile** do **not support list values**, which can cause errors when saving the data.


In [6]:
for col in buildings.columns:
    if any(isinstance(val, list) for val in buildings[col]):
        buildings = buildings.astype({col: str})

- It loops through each column in `buildings`.
- For each column, it checks if **any of the values** in that column are lists.
- If so, it **converts the entire column to strings** using `astype({col: str})`, so that lists become plain text (e.g., `"['shop', 'office']"`).


### Saving to file


In [7]:
#buildings.to_file('../data/osm_build.geojson')

This command saves the `buildings` GeoDataFrame to a **GeoJSON** file, which can then be opened in any GIS software or reused in other projects.
The file format is automatically determined by the file extension (`.geojson` in this case).


## Summary


In this section, we explored how to access and use **OpenStreetMap (OSM)** data directly in Python using the **OSMnx** library.

We learned how to:

- Define an area of interest by name and retrieve its boundaries
- Download OSM data such as **buildings** or **street networks**
- Convert OSM data into `GeoDataFrames` for further spatial analysis
- Visualize the results on an interactive map — without leaving the notebook

Using OSMnx, we can quickly integrate real-world, up-to-date geographic data into our analysis workflows — making OSM a powerful and accessible data source for spatial projects.
